In [1]:
import delfi.distribution as dd
import delfi.generator as dg
import delfi.inference as infer
import delfi.utils.io as io
import delfi.summarystats as ds
import numpy as np
import os
import scipy.misc
import sys
import sys 
sys.path.append('../../')
from model_comparison.models import BaseModel
import matplotlib.pyplot as plt


In [2]:
def calc_dist(stats_1, stats_2):
    """Euclidian distance between summary statistics"""
    return np.sqrt(np.sum((stats_1 - stats_2) ** 2))

def discrete_sample(p, n_samples=1):
    """
    Samples from a discrete distribution.
    :param p: a distribution with N elements
    :param n_samples: number of samples
    :return: vector of samples
    """

    # check distribution
    #assert isdistribution(p), 'Probabilities must be non-negative and sum to one.'

    # cumulative distribution
    c = np.cumsum(p[:-1])[np.newaxis, :]

    # get the samples
    r = np.random.rand(n_samples, 1)
    return np.sum((r > c).astype(int), axis=1)

In [4]:
def rejection_abc(model_list, model_prior, prior_list, summary_list, obs_stats, n_params, seed=None, tol=2, step=0.1, n_samples=5e7): 
    
    # sample a model 
    
    # sample parameters 
    
    # sample data 
    
    # compare and decide 
    
    # return posterior estimate
    pass
    
    
def rejection_sampling_abc(sxo, models, model_priors, param_priors, niter=10000, verbose=False, eps=1e-1):
    """
    Basic rejection sampling algorithm including estimate of the model posterior.

    Takes mean and var of data vector as summary stats.

    :param sxo: observed summary stats
    :param models: list with scipy.stats objects
    :param model_priors: list of model prior probs, summing to 1
    :param param_priors: list of lists containing the scipy.stats prior objects for every model
    :param niter: number of iterations
    :param verbose: no pbar if False
    :param eps: rejection criterion.
    :return: list of accepted model indices, list of lists of accepted parameters, list of differences for every it.
    """
    n_models = len(models)

    accepted_its = []
    accepted_mi = []
    accepted_params = [[] for n in range(n_models)]
    differences = []

    for it in tqdm.tqdm(range(niter), disable=not verbose):
        # sample model index
        mi = np.where(np.random.multinomial(n=1, pvals=model_priors))[0][0]

        # get model and prior
        m = models[mi]
        priors = param_priors[mi]
        # sample corresponding params
        params = [prior.rvs() for prior in priors]
        # get data and stats
        x = m.gen([params])
        sx = np.array([x.mean(), x.var()])
        # take diff
        d = np.abs(sxo - sx).sum()
        differences.append(d)
        if d < eps:
            accepted_its.append(it)
            accepted_params[mi].append(params)
            accepted_mi.append(mi)

    return accepted_mi, accepted_params, differences

In [5]:
def run_mcmc(model, prior, summary, obs_stats, n_params, seed=None, tol=2, step=0.1, n_samples=5e7):
    """Runs MCMC-ABC algorithm.
    Adapted from epsilonfree code https://raw.githubusercontent.com/gpapamak/epsilon_free_inference/8c237acdb2749f3a340919bf40014e0922821b86/demos/mg1_queue_demo/mg1_abc.py
    Parameters
    ----------
    model : 
         Model
    prior :
         Prior
    summary :
         Function to compute summary statistics
    obs_stats: 
         Observed summary statistics
    n_params : 
         Number of parameters
    seed : int or None
        If set, randomness in sampling is disabled
    tol : float
        Tolerance for MCMC-ABC
    step : float
        Step for MCMC-ABC
    n_samples : int
        Number of simulations for MCMC-ABC
    """
    # check for subfolders, create if they don't exist
    dirs = {}
    dirs['dir_abc'] = './results/abc/'
    for k, v in dirs.items():
        if not os.path.exists(v):
            os.makedirs(v)
            
    prefix = str(n_params)+'params'
    
    #####################
    np.random.seed(seed)
    
    n_sims = 0
    n_samples = int(n_samples)

    # initialize markov chain with a parameter whose distance is within tolerance
    num_init_sims = int(1e5)
    for i in range(num_init_sims):
        ps = prior.gen(n_samples=1)[0]
        states = model.gen_single(ps)
        stats = summary.calc([states])
        dist = calc_dist(stats, obs_stats)
        if dist < tol:
            cur_ps = ps
            cur_stats = stats
            cur_dist = dist
            break
    else:
        raise ValueError('No parameter was found with distance within tolerance.')

    # simulate markov chain
    ps = [cur_ps.copy()]
    stats = [cur_stats.copy()]
    dist = [cur_dist]
    n_accepted = 0

    for i in range(n_samples):

        prop_ps = cur_ps + step * np.random.randn(n_params)
        states = model.gen_single(prop_ps)
        prop_stats = summary.calc([states])
        prop_dist = calc_dist(prop_stats, obs_stats)
        n_sims += 1

        # acceptance / rejection step
        #if prop_dist < tol and np.all(prop_ps <= prior_max) and np.all(prop_ps >= prior_min):
        if prop_dist < tol and np.random.rand() < np.exp(prior.eval(prop_ps[np.newaxis, :], log=True) - prior.eval(cur_ps[np.newaxis, :], log=True)):
            cur_ps = prop_ps
            cur_stats = prop_stats
            cur_dist = prop_dist
            n_accepted += 1

        ps.append(cur_ps.copy())
        stats.append(cur_stats.copy())
        dist.append(cur_dist)

        print('simulation {0}, distance = {1}, acc rate = {2:%}'.format(i, cur_dist, float(n_accepted) / (i+1)))

    ps = np.array(ps)
    stats = np.array(stats)
    dist = np.array(dist)
    acc_rate = float(n_accepted) / n_samples

    return ps, stats, dist, acc_rate, n_sims

In [6]:
from delfi.simulator import Gauss

n_params = 1
m = Gauss(dim=n_params)
p = dd.Uniform(lower=[-10], upper=[10])
s = ds.Identity()

In [7]:
x = scipy.stats.norm.rvs(1)
xo = scipy.stats.norm.rvs(1)

In [8]:
ps, stats, dist, acc_rate, n_sims = run_mcmc(model=m, prior=p, summary=s, obs_stats=[xo], n_params=1, n_samples=1e5)

simulation 0, distance = 1.693295124666311, acc rate = 100.000000%
simulation 1, distance = 0.7393407002027241, acc rate = 100.000000%
simulation 2, distance = 1.818982891530628, acc rate = 100.000000%
simulation 3, distance = 1.7097624752417246, acc rate = 100.000000%
simulation 4, distance = 1.252990415527666, acc rate = 100.000000%
simulation 5, distance = 1.610072770067812, acc rate = 100.000000%
simulation 6, distance = 1.610072770067812, acc rate = 85.714286%
simulation 7, distance = 1.3477877370209201, acc rate = 87.500000%
simulation 8, distance = 1.8021713643844897, acc rate = 88.888889%
simulation 9, distance = 1.919483279019885, acc rate = 90.000000%
simulation 10, distance = 1.6845909386003766, acc rate = 90.909091%
simulation 11, distance = 1.2357506076485105, acc rate = 91.666667%
simulation 12, distance = 1.984707868645791, acc rate = 92.307692%
simulation 13, distance = 1.984707868645791, acc rate = 85.714286%
simulation 14, distance = 1.8631837486589022, acc rate = 86.

simulation 514, distance = 1.4197570457445652, acc rate = 84.077670%
simulation 515, distance = 1.1720207225348784, acc rate = 84.108527%
simulation 516, distance = 1.5503916094323034, acc rate = 84.139265%
simulation 517, distance = 0.9749336965287108, acc rate = 84.169884%
simulation 518, distance = 0.979089018750367, acc rate = 84.200385%
simulation 519, distance = 1.706894851593393, acc rate = 84.230769%
simulation 520, distance = 0.9781653051447892, acc rate = 84.261036%
simulation 521, distance = 0.9591613225969874, acc rate = 84.291188%
simulation 522, distance = 1.3457312383968254, acc rate = 84.321224%
simulation 523, distance = 0.6871655980582674, acc rate = 84.351145%
simulation 524, distance = 0.6473437425301993, acc rate = 84.380952%
simulation 525, distance = 1.4827132977335942, acc rate = 84.410646%
simulation 526, distance = 0.7980808847576597, acc rate = 84.440228%
simulation 527, distance = 1.5883216934614635, acc rate = 84.469697%
simulation 528, distance = 0.9879940

simulation 1014, distance = 1.5455146570626397, acc rate = 90.246305%
simulation 1015, distance = 1.5223672157462058, acc rate = 90.255906%
simulation 1016, distance = 0.5674505667905678, acc rate = 90.265487%
simulation 1017, distance = 0.7760369055134759, acc rate = 90.275049%
simulation 1018, distance = 1.0748098379215552, acc rate = 90.284593%
simulation 1019, distance = 1.5596086497839583, acc rate = 90.294118%
simulation 1020, distance = 1.3352462720447242, acc rate = 90.303624%
simulation 1021, distance = 0.5624846235542313, acc rate = 90.313112%
simulation 1022, distance = 0.4733604931239106, acc rate = 90.322581%
simulation 1023, distance = 0.8680565034003443, acc rate = 90.332031%
simulation 1024, distance = 0.5765199729886019, acc rate = 90.341463%
simulation 1025, distance = 0.4704589052227466, acc rate = 90.350877%
simulation 1026, distance = 0.6503891453834623, acc rate = 90.360273%
simulation 1027, distance = 0.14310330509410063, acc rate = 90.369650%
simulation 1028, di

simulation 1510, distance = 1.6305786570529932, acc rate = 92.918597%
simulation 1511, distance = 1.2203424933529488, acc rate = 92.923280%
simulation 1512, distance = 1.4416129686422128, acc rate = 92.927958%
simulation 1513, distance = 1.6576726462695597, acc rate = 92.932629%
simulation 1514, distance = 1.9224080799760181, acc rate = 92.937294%
simulation 1515, distance = 1.5040830451428786, acc rate = 92.941953%
simulation 1516, distance = 1.557364073309786, acc rate = 92.946605%
simulation 1517, distance = 1.557364073309786, acc rate = 92.885375%
simulation 1518, distance = 1.632215152195094, acc rate = 92.890059%
simulation 1519, distance = 1.5779138394857293, acc rate = 92.894737%
simulation 1520, distance = 1.3945441462015646, acc rate = 92.899408%
simulation 1521, distance = 1.8677003605638423, acc rate = 92.904074%
simulation 1522, distance = 1.9529888914846691, acc rate = 92.908733%
simulation 1523, distance = 1.9529888914846691, acc rate = 92.847769%
simulation 1524, distan

simulation 1992, distance = 0.06771867545993548, acc rate = 94.129453%
simulation 1993, distance = 0.720871493322026, acc rate = 94.132397%
simulation 1994, distance = 0.07110264188787796, acc rate = 94.135338%
simulation 1995, distance = 0.5648529339256101, acc rate = 94.138277%
simulation 1996, distance = 0.13359888597071157, acc rate = 94.141212%
simulation 1997, distance = 0.29306471810438284, acc rate = 94.144144%
simulation 1998, distance = 0.7465868660551914, acc rate = 94.147074%
simulation 1999, distance = 0.533658308882101, acc rate = 94.150000%
simulation 2000, distance = 0.010496341104085483, acc rate = 94.152924%
simulation 2001, distance = 0.8166703786744075, acc rate = 94.155844%
simulation 2002, distance = 0.5261337225240987, acc rate = 94.158762%
simulation 2003, distance = 1.619646066576291, acc rate = 94.161677%
simulation 2004, distance = 1.224909740691565, acc rate = 94.164589%
simulation 2005, distance = 0.9413696182219584, acc rate = 94.167498%
simulation 2006, d

...

simulation 97642, distance = 0.37438554063231155, acc rate = 91.459705%
simulation 97643, distance = 0.02756511065138767, acc rate = 91.459793%
simulation 97644, distance = 0.5415819434860034, acc rate = 91.459880%
simulation 97645, distance = 0.5776049888986368, acc rate = 91.459968%
simulation 97646, distance = 0.46492567739174007, acc rate = 91.460055%
simulation 97647, distance = 0.6981141208352506, acc rate = 91.460143%
simulation 97648, distance = 0.1295246090850637, acc rate = 91.460230%
simulation 97649, distance = 0.6423526224203111, acc rate = 91.460317%
simulation 97650, distance = 0.7975340373934698, acc rate = 91.460405%
simulation 97651, distance = 0.8081902763342139, acc rate = 91.460492%
simulation 97652, distance = 0.36625175223844453, acc rate = 91.460580%
simulation 97653, distance = 1.004817839980403, acc rate = 91.460667%
simulation 97654, distance = 0.8647066106868069, acc rate = 91.460755%
simulation 97655, distance = 0.5371659882258348, acc rate = 91.460842%
sim

simulation 98130, distance = 0.3659618762538934, acc rate = 91.424728%
simulation 98131, distance = 0.04536580419025782, acc rate = 91.424816%
simulation 98132, distance = 0.5518907534205759, acc rate = 91.424903%
simulation 98133, distance = 0.2476164723889227, acc rate = 91.424990%
simulation 98134, distance = 0.40790113309222, acc rate = 91.425078%
simulation 98135, distance = 0.5529432013199931, acc rate = 91.425165%
simulation 98136, distance = 0.06098858894290271, acc rate = 91.425252%
simulation 98137, distance = 0.028613989356007785, acc rate = 91.425340%
simulation 98138, distance = 0.19342131890635406, acc rate = 91.425427%
simulation 98139, distance = 0.3142732410689728, acc rate = 91.425515%
simulation 98140, distance = 0.17328223894044092, acc rate = 91.425602%
simulation 98141, distance = 0.1122552332108524, acc rate = 91.425689%
simulation 98142, distance = 0.7095723442462332, acc rate = 91.425777%
simulation 98143, distance = 0.40469437776562955, acc rate = 91.425864%
s

simulation 98613, distance = 0.23282011986883444, acc rate = 91.441377%
simulation 98614, distance = 0.05398085369993133, acc rate = 91.441464%
simulation 98615, distance = 0.07813083182880809, acc rate = 91.441551%
simulation 98616, distance = 1.0948039698673515, acc rate = 91.441638%
simulation 98617, distance = 0.5286100808733356, acc rate = 91.441725%
simulation 98618, distance = 0.4944247832246722, acc rate = 91.441811%
simulation 98619, distance = 0.6727406739408224, acc rate = 91.441898%
simulation 98620, distance = 0.7113782868821072, acc rate = 91.441985%
simulation 98621, distance = 0.7962549450550886, acc rate = 91.442072%
simulation 98622, distance = 0.3741188532598483, acc rate = 91.442159%
simulation 98623, distance = 0.7839304893638088, acc rate = 91.442245%
simulation 98624, distance = 0.9301464057097393, acc rate = 91.442332%
simulation 98625, distance = 0.9504656772914499, acc rate = 91.442419%
simulation 98626, distance = 1.0907232394196802, acc rate = 91.442506%
sim

simulation 99082, distance = 0.37354069069859497, acc rate = 91.472806%
simulation 99083, distance = 0.19888418734045898, acc rate = 91.472892%
simulation 99084, distance = 0.2740401715770815, acc rate = 91.472978%
simulation 99085, distance = 0.101040132752793, acc rate = 91.473064%
simulation 99086, distance = 0.2946379117642999, acc rate = 91.473150%
simulation 99087, distance = 0.43856725363504623, acc rate = 91.473236%
simulation 99088, distance = 0.5019014518046103, acc rate = 91.473322%
simulation 99089, distance = 1.0117876196939286, acc rate = 91.473408%
simulation 99090, distance = 0.6090207094486182, acc rate = 91.473494%
simulation 99091, distance = 0.5005812649812809, acc rate = 91.473580%
simulation 99092, distance = 0.6521072770269463, acc rate = 91.473666%
simulation 99093, distance = 0.4179375544660089, acc rate = 91.473752%
simulation 99094, distance = 0.5443967424133072, acc rate = 91.473838%
simulation 99095, distance = 0.042215183856934235, acc rate = 91.473924%
si

simulation 99570, distance = 1.3141020289631036, acc rate = 91.513593%
simulation 99571, distance = 0.9657179636622335, acc rate = 91.513679%
simulation 99572, distance = 1.0348124071389697, acc rate = 91.513764%
simulation 99573, distance = 1.315790819428472, acc rate = 91.513849%
simulation 99574, distance = 1.3624153316206247, acc rate = 91.513934%
simulation 99575, distance = 1.1449024788415905, acc rate = 91.514019%
simulation 99576, distance = 1.4527224097256717, acc rate = 91.514105%
simulation 99577, distance = 1.7759996728549874, acc rate = 91.514190%
simulation 99578, distance = 1.061424497627446, acc rate = 91.514275%
simulation 99579, distance = 1.2469227800806943, acc rate = 91.514360%
simulation 99580, distance = 1.4272669975304941, acc rate = 91.514446%
simulation 99581, distance = 0.3079920324139891, acc rate = 91.514531%
simulation 99582, distance = 1.6781103004490154, acc rate = 91.514616%
simulation 99583, distance = 1.5660463642181686, acc rate = 91.514701%
simulati

In [ ]:
from delfi.inference import Basic
from delfi.generator import Default

g = Default(model=m, prior=p, summary=s)
inf_basic = Basic(generator=g, n_components=1, n_hiddens=[10])

In [ ]:
log, train_data, _ = inf_basic.run(n_train=5000, n_rounds=1)

In [ ]:
plt.plot(log[0]['loss'])
plt.xlabel('Iteration')
plt.ylabel('Loss');

In [ ]:
xo = np.array([[0.]])
posterior = inf_basic.predict(xo)

In [ ]:
for k in range(1):
    print(r'component {}: mixture weight = {:.2f}; mean = {:.2f}; variance = {:.2f}'.format(
        k+1, posterior.a[k], posterior.xs[k].m[0], posterior.xs[k].S[0][0]))

In [ ]:
true_posterior = dd.MoG(a=[0.5, 0.5], ms=[[0.], [0.]], Ss=[[[1.0]], [[0.1]]])

In [ ]:
plt.hist(ps, bins='auto');
plt.twinx()
plt.plot(np.arange(-5.0, 5.0, 0.01), posterior.eval(np.arange(-5.0, 5.0, 0.01).reshape(-1,1), log=False), '-b')
plt.plot(np.arange(-5.0, 5.0, 0.01), true_posterior.eval(np.arange(-5.0, 5.0, 0.01).reshape(-1,1), log=False), '-r')
plt.legend(['predicted posterior', 'true posterior'], frameon=False)
plt.axis('off');